### Economic Activity Coding

---

In [3]:
import csv
from collections import Counter
import numpy as np
from sklearn.model_selection import train_test_split
import re
from keras.preprocessing.text import Tokenizer
from scipy import sparse
from sklearn.metrics import accuracy_score, confusion_matrix, f1_score, precision_recall_fscore_support, roc_auc_score
from sklearn import preprocessing
import time
import pandas as pd
from scipy.sparse import hstack
import pickle
from sklearn.metrics import accuracy_score
from sklearn.svm import LinearSVC
from sklearn.ensemble import RandomForestClassifier
from sklearn.neural_network import MLPClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.tree import DecisionTreeClassifier
from sklearn.naive_bayes import GaussianNB
from sklearn.neighbors import KNeighborsClassifier
from xgboost import XGBClassifier
from sklearn.ensemble import ExtraTreesClassifier
import scipy
from keras.utils import to_categorical

Using TensorFlow backend.


In [4]:
####  DATA BASE
file4 = pd.read_excel(r'/home/alejandro/Desktop/ENIGHS/ENIGH_2018.xlsx')

In [5]:
# Economic Activity variable (SCIAN):
SCIAN = list(file4.SCIAN)

In [6]:
####  FEATURES

# Main Variables - Textual Features:
NOM_OCUP = list(file4.NOM_OCUP_S)
TAREA_OCUP = list(file4.TAREA_OCUP_S)
ACT_EMP = list(file4.ACT_EMP_S)
NOM_EMP = list(file4.NOM_EMP_S)

ALL_TXT = [str(i) + ' ' + str(j) + ' ' + str(k) + ' ' + str(l) for i,j,k,l in zip(NOM_OCUP,TAREA_OCUP,ACT_EMP,NOM_EMP)]

# Auxiliary Variables - categorical features:
OTRAS = [[str(i) if not np.isnan(i) else '' for i in [i1,i2,i3,i4,i5,i6,i7,i8,i9,i10,i11]] for i1,i2,i3,i4,i5,i6,i7,i8,i9,i10,i11 in zip(file4.LUG_ACT,file4.CLAS_EMP,file4.PERSONAL,file4.PAGO,file4.TRA_PAIS,file4.TAM_EMP,file4.NIVEL_APROB,file4.GRADO_APROB,file4.NIVEL,file4.GRADO,file4.NOM_EMPD)]



In [7]:
IND_SCIAN = list(file4.IND_SCIAN)

In [8]:
SCIAN_freqs = sorted(Counter(SCIAN).items(), key=lambda tup: tup[1], reverse=True)
DICT_SCIAN_Y = { pair[0]:y for pair, y in zip(SCIAN_freqs, range(len(SCIAN_freqs)))}
DICT_Y_SCIAN = { y:pair[0] for pair, y in zip(SCIAN_freqs, range(len(SCIAN_freqs)))}
Y_SCIAN = [ DICT_SCIAN_Y[y] for y in SCIAN]
DICT_SCIAN_FREQ = dict(SCIAN_freqs)
YFREQ_SCIAN = [ DICT_SCIAN_FREQ[y] for y in SCIAN]


inds = np.where(np.array(YFREQ_SCIAN) >= 4)

import numpy as np
npALL_TXT = np.array(ALL_TXT)
npIND_SCIAN= np.array(IND_SCIAN)
int_OTRAS = []
for row in OTRAS:
    int_row = []
    for e in row:
        int_row += [int(float(e)) if e is not '' else 0]
    int_OTRAS += [int_row]
npOTRAS = np.array(int_OTRAS)
npY_SCIAN = np.array(Y_SCIAN)

In [9]:
y_train_IND_SCIAN,y_test_IND_SCIAN,OTRAS_train, OTRAS_test, X_train_p, X_test_p, y_train, y_test = train_test_split(npIND_SCIAN[inds],npOTRAS[inds], npALL_TXT[inds], npY_SCIAN[inds],
                                                    stratify=npY_SCIAN[inds], 
                                                    test_size=0.25, 
                                                    random_state=1)

In [10]:
def char_ngrams(string, nlen):
        inputstring = string
        c = re.compile(r"\s")
        inputstring = inputstring.strip()
        inputstring = c.sub("~", inputstring)
        return " ".join([inputstring[x:x+nlen] for x in range(len(inputstring)-nlen+1)])
    
def ngram_palcom(string, n):
    sp=string.split(' ')
    if sp[-1]=='':
        sp.remove('')
    inputstring = ['~'.join(sp[m:m+n]) for m in range(0,len(sp)+1 -n)]
    return ' '.join(inputstring)

def votacion(el):
    return sorted([[el.count(i),i]  for i in list(set(el))])[-1][-1]

def vot(lis,y_test,opcion):
    y_p= [votacion([i[k] for i in lis]) for k in range(len(y_test))]
    if opcion==1:
        return accuracy_score(y_test,y_p)
    elif opcion==2:
        return y_p
    elif opcion==3:
        return precision_recall_fscore_support(y_test,y_p,average='macro')


In [11]:
X_train1 = [char_ngrams(txt, 6).lower() for txt in X_train_p]
X_test1 = [char_ngrams(txt, 6).lower() for txt in X_test_p]

In [12]:
X_train2 = [ngram_palcom(txt, 2).lower() for txt in X_train_p] 
X_test2 = [ngram_palcom(txt, 2).lower() for txt in X_test_p]

In [13]:
x_tok = [char_ngrams(txt, 6).lower() for txt in npALL_TXT]
x_tok2 = [ngram_palcom(txt, 2).lower() for txt in npALL_TXT]

In [14]:
vocab_size = 30000  
tokenizer = Tokenizer(num_words=vocab_size)
tokenizer.fit_on_texts(x_tok)
TR1 = tokenizer.texts_to_matrix(X_train1, mode="tfidf")
TE1 = tokenizer.texts_to_matrix(X_test1, mode="tfidf")


In [15]:
vocab_size = 30000
tokenizer = Tokenizer(num_words=vocab_size)
tokenizer.fit_on_texts(x_tok2)
TR2 = tokenizer.texts_to_matrix(X_train2, mode="tfidf")
TE2 = tokenizer.texts_to_matrix(X_test2, mode="tfidf")

In [16]:
TTR1=sparse.csr_matrix(TR1)
TTR2=sparse.csr_matrix(TR2)

In [17]:
TTE1=sparse.csr_matrix(TE1)
TTE2=sparse.csr_matrix(TE2)

In [18]:
TR=hstack((TTR1,TTR2))

In [19]:
TE=hstack((TTE1,TTE2))

In [20]:
X = hstack((preprocessing.normalize(TR, norm='l2'),OTRAS_train))
con_x_test = hstack((preprocessing.normalize(TE, norm='l2'),OTRAS_test))

In [ ]:
g1=LinearSVC(class_weight='balanced')
g2=RandomForestClassifier()
g3=MLPClassifier()
g4=LogisticRegression(max_iter=2500)
g5=DecisionTreeClassifier()
g6=GaussianNB()
g7=KNeighborsClassifier()
g8=XGBClassifier()
g9=ExtraTreesClassifier()

todos_predictos=[]
for i,j in zip([g1,g2,g3,g4,g5,g6,g7,g8,g9],['svm','rfc','mlpc','lr','dtc','gnb','knc','xgboost','etc']):
    a=time.time()
    if j!='gnb':
        i.fit(X,y_train)
    else:
        i.fit(X.toarray(),y_train)
    b=time.time()-a
    if j!='gnb':
        y_pr=i.predict(con_x_test)
    else:
        y_pr=i.predict(con_x_test.toarray())
    todos_predictos.append(y_pr)
    print('{} --> acc: {} tiempo: {} min'.format(j,accuracy_score(y_test,y_pr),b/60))

/home/alejandro/.local/lib/python3.6/site-packages/sklearn/svm/_base.py:947: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)


svm --> acc: 0.8798254024322552 tiempo: 22.225339555740355 min
rfc --> acc: 0.8405409496896604 tiempo: 8.932241888840993 min


In [ ]:
y_p1=todos_predictos[0] #svm
y_p2=todos_predictos[1] #rfc
y_p3=todos_predictos[2] #mlpc
y_p4=todos_predictos[3] #lr
y_p5=todos_predictos[4] #dtc
y_p6=todos_predictos[5] #gnb
y_p7=todos_predictos[6] #knc
y_p8=todos_predictos[7] #xgboost
y_p9=todos_predictos[8] #etc

In [ ]:
ensamble_predichos=[y_p1,y_p1,y_p1,y_p1,y_p4,y_p4,y_p2,y_p3,y_p3,y_p3,y_p8,y_p8,y_p7,y_p6,y_p5,y_p5,y_p5]
y_predicto=vot(ensamble_predichos,y_test,1)#opcion 1-accuracy 2-predichos 3-otras metricas